In [1]:
#SFT 
from unsloth import FastLanguageModel
import torch
max_seq_length = 2048*4 # Choose any! We auto support RoPE Scaling internally!
dtype = None # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True # Use 4bit quantization to reduce memory usage. Can be False.
datapath = 'readsy/stories/'
pairpath = 'readsy/pairs/readsy_story_pairs0407.csv'
mode='m3'
split_by = 'genre'
model_name = 'model/gemma/gemma-2b/'
lease_likes = 10
suffix = 'vast'
save_path = 'model/SFTmodels/' +model_name.split('/')[-1] + '_sft' + mode + split_by + str(lease_likes) + suffix


🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


In [2]:
model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = model_name, # Choose ANY! eg teknium/OpenHermes-2.5-Mistral-7B
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
    # token = "hf_...", # use one if using gated models like meta-llama/Llama-2-7b-hf
)
model = FastLanguageModel.get_peft_model(
    model,
    use_gradient_checkpointing = "unsloth",
    r = 16, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 16,
    lora_dropout = 0, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    random_state = 3407,
    use_rslora = False,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)


==((====))==  Unsloth: Fast Gemma patching release 2024.5
   \\   /|    GPU: NVIDIA GeForce RTX 4090. Max memory: 23.643 GB. Platform = Linux.
O^O/ \_/ \    Pytorch: 2.2.0+cu121. CUDA = 8.9. CUDA Toolkit = 12.1.
\        /    Bfloat16 = TRUE. Xformers = 0.0.24. FA = True.
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth


`config.hidden_act` is ignored, you should use `config.hidden_activation` instead.
Gemma's activation function will be set to `gelu_pytorch_tanh`. Please, use
`config.hidden_activation` if you want to override this behaviour.
See https://github.com/huggingface/transformers/pull/29402 for more details.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Unsloth 2024.5 patched 18 layers with 18 QKV layers, 18 O layers and 18 MLP layers.


In [7]:
from dataloader import StoryPairDataset
SPdataloader = StoryPairDataset(datapath,
                              pairpath,
                              tokenizer,
                              task='sft',
                              used_dataset_size=100,
                              train_test_split=0.1,
                              split_by=split_by,
                              max_len=4096,
                              mode= mode,
                              max_time_window=3600,
                              least_likes= lease_likes,
                              margin=False)



the total number of pairs is  100
the number of effective pairs is  90
Index(['prompt_id', 'prompt', 'story_id', 'story_title', 'story_author',
       'story_url', 'link', 'genre', 'is_sensitive', 'categories', 'likes',
       'story_text', 'posted_date', 'comments'],
      dtype='object')
{'Horror': 10, 'Middle School': 7, 'Dialogue': 6, 'Angst': 5, 'Kids': 5, 'Thriller and Suspense': 5, 'Novel': 5, 'Science Fiction': 5, 'Romance': 5, 'Adventure': 4, 'Narrative': 3, 'Winter': 3, 'Fluff': 3, 'Mystery': 3, 'Character': 3, 'Teens': 2, 'Dramatic': 2, 'Funny': 2, 'Sad': 2, 'Adults': 2, 'High School': 2, "Valentine's Day": 1, 'Short Story': 1, 'Summer': 1, 'Holiday': 1, 'Christmas': 1, 'Fiction': 1}
the genre of test set is  ['Horror']
the percentage of test set is  0.1111111111111111 where total is  90


No chat template is set for this tokenizer, falling back to a default class-level template. This is very error-prone, because models are often trained with templates different from the class default! Default chat templates are a legacy feature and will be removed in Transformers v4.43, at which point any code depending on them will stop working. We recommend setting a valid chat template before then to ensure that this model continues working without issues.


the columns of train is  Index(['story1_id', 'story2_id', 'prompt_id'], dtype='object')
the first example of train is  story1_id                                               7gz4qo
story2_id                                               7gz4qo
prompt_id                                          prompt_0156
text         <bos><|im_start|>user\nWrite a story where a c...
Name: 0, dtype: object


In [15]:
save_path = 'model/SFTmodels/' +model_name.split('/')[-2] + '_sft' + mode + split_by + str(lease_likes) + suffix
from trl import SFTTrainer
from transformers import TrainingArguments

trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = SPdataloader.dataset["train"],
    eval_dataset = SPdataloader.dataset["test"],
    dataset_text_field = "text",
    max_seq_length = max_seq_length,
    dataset_num_proc = 1,
    packing = True, # Can make training 5x faster for short sequences.
    args = TrainingArguments(
        per_device_train_batch_size = 1,
        gradient_accumulation_steps = 2,
        warmup_steps = 5,
        num_train_epochs = 1,
        learning_rate = 1e-4,
        fp16 = not torch.cuda.is_bf16_supported(),
        bf16 = torch.cuda.is_bf16_supported(),
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.01,
        lr_scheduler_type = "cosine",
        seed = 3407,
        output_dir = save_path,
    ),
)
trainer.train()
#save the model AND the tokenizer
trainer.save_model(save_path)
#trainer.save_tokenizer(save_path)
print('model saved at', save_path)

Detected kernel version 5.4.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.
==((====))==  Unsloth - 2x faster free finetuning | Num GPUs = 1
   \\   /|    Num examples = 48 | Num Epochs = 1
O^O/ \_/ \    Batch size per device = 2 | Gradient Accumulation steps = 2
\        /    Total batch size = 4 | Total steps = 12
 "-____-"     Number of trainable parameters = 19,611,648


OutOfMemoryError: CUDA out of memory. Tried to allocate 15.62 GiB. GPU 0 has a total capacity of 23.64 GiB of which 10.97 GiB is free. Process 1232897 has 12.67 GiB memory in use. Of the allocated memory 12.13 GiB is allocated by PyTorch, and 82.25 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

In [10]:



def generate(model, tokenizer, prompt, max_length=1024*4):
    chat = [
        {"role":"user", "content":prompt},
    ]
    inputs = tokenizer.apply_chat_template(chat, tokenize = False, add_generation_prompt = True)
    #add bos token
    inputs = tokenizer.bos_token + inputs
    print("inputs:", inputs)
    inputs = tokenizer.encode(inputs, add_special_tokens=True, return_tensors="pt")
    print("inputs encoded:", inputs)
    # Move inputs to GPU
    inputs = inputs.to("cuda")
    
    outputs = model.generate(input_ids=inputs, max_new_tokens = max_length, min_new_tokens = 500)
    #decode the outputs
    outputs = tokenizer.decode(outputs[0], skip_special_tokens=False)
    return outputs



prompt = "Write a story about discovering a lost manuscript. It can be from a famous (or infamous) author, or an unknown one."
print("Prompt:", prompt)
outputs = generate(model, tokenizer, prompt)
print('written by the model:', model_path)  
print("Generated story:", outputs)
print("Length of the generated story:", len(outputs.split()))

Prompt: Write a story about discovering a lost manuscript. It can be from a famous (or infamous) author, or an unknown one.
inputs: <bos><|im_start|>user
Write a story about discovering a lost manuscript. It can be from a famous (or infamous) author, or an unknown one.<|im_end|>
<|im_start|>assistant

inputs encoded: tensor([[     2,      2, 235322, 235371,    571, 235298,   2997,  73786,   1645,
            108,   5559,    476,   3904,   1105,  59551,    476,   5501,  28086,
         235265,   1165,    798,    614,    774,    476,  10964,    591,    483,
          76100, 235275,   3426, 235269,    689,    671,  12417,    974,  35606,
         235371,    571, 235298,    615,  73786,    108, 235322, 235371,    571,
         235298,   2997,  73786, 105776,    108]])


KeyboardInterrupt: 

In [11]:
save_path = 'model/SFTmodels/' +model_name.split('/')[-2] + '_sft' + mode + split_by + str(lease_likes) + suffix
save_path

'model/SFTmodels/gemma-2b_sftm3genre10vast'

'<pad>'